### Libraries

In [1]:
from torch.utils.data import DataLoader, random_split
from torch.optim import Adam, RMSprop

In [2]:
from data.preprocessing import *
from data.data_utils import *
from models.macro_architectures import *
from utils import *


# DATA

In [9]:
#format: YYYYMMDD
start_time = '20210101'
end_time = '20230802'
scrap_date = interval_time(start_time, end_time)

In [10]:
months = list(set([day[:6] for day in scrap_date]))
import_Dst(months)

In [11]:
l1_sample, l2_sample, dst, kp = automated_preprocessing(scrap_date, sep = False)

# L1 (raw) data

## Minute based

In [12]:
l1_sample

proton_vx_gse  proton_vy_gse  proton_vz_gse  \
2021-01-01 00:00:00     -376.20000       4.962500      33.550000   
2021-01-01 00:01:00     -376.94998       4.875000      33.887500   
2021-01-01 00:02:00     -375.73750       4.575000      36.800000   
2021-01-01 00:03:00     -376.43332       4.388889      37.688890   
2021-01-01 00:04:00     -378.28750       5.262500      34.675000   
...                            ...            ...            ...   
2023-08-02 23:55:00     -355.38890      20.311111     -22.777779   
2023-08-02 23:56:00     -350.30000      13.860001     -27.279999   
2023-08-02 23:57:00     -356.23330      19.755556     -22.733334   
2023-08-02 23:58:00     -353.00000      11.433333     -27.388890   
2023-08-02 23:59:00     -352.80000       9.688889     -30.111110   

                     proton_vx_gsm  proton_vy_gsm  proton_vz_gsm  \
2021-01-01 00:00:00     -376.20000      -3.637500      33.737500   
2021-01-01 00:01:00     -376.94998      -3.775000      34.000000   
2021-01-01 00:02:00     -375.73750      -4.825000      36.737500   
2021-01-01 00:03:00     -376.43332      -5.222222      37.566666   
2021-01-01 00:04:00     -378.28750      -3.625000      34.862500   
...                            ...            ...            ...   
2023-08-02 23:55:00     -355.38890      17.633333     -24.888890   
2023-08-02 23:56:00     -350.30000      10.719999     -28.660000   
2023-08-02 23:57:00     -356.23330      17.099998     -24.788889   
2023-08-02 23:58:00     -353.00000       8.288889     -28.488888   
2023-08-02 23:59:00     -352.80000       6.244444     -30.988888   

                     proton_speed  proton_density  proton_temperature  \
2021-01-01 00:00:00     377.75000        4.115000           56242.375   
2021-01-01 00:01:00     378.51248        4.246250           52797.875   
2021-01-01 00:02:00     377.58750        4.012500           49726.500   
2021-01-01 00:03:00     378.36667        3.981111           50515.000   
2021-01-01 00:04:00     379.95000        4.075000           54038.500   
...                           ...             ...                 ...   
2023-08-02 23:55:00     356.73334       11.565556           47607.668   
2023-08-02 23:56:00     351.70000       10.184000           40658.900   
2023-08-02 23:57:00     357.56668       11.521111           50020.668   
2023-08-02 23:58:00     354.26666       10.534444           45901.777   
2023-08-02 23:59:00     354.26666       10.708889           52269.890   

                           bt    bx_gse    by_gse    bz_gse  theta_gse  \
2021-01-01 00:00:00  3.026571 -0.909816 -1.326903  2.519875  57.259254   
2021-01-01 00:01:00  2.980888 -1.039568 -1.586296  2.293360  50.340990   
2021-01-01 00:02:00  2.988627 -1.012260 -1.607630  2.289666  50.247160   
2021-01-01 00:03:00  2.970987 -1.226179 -1.654866  2.102007  45.554783   
2021-01-01 00:04:00  2.999099 -1.335279 -1.652042  2.094897  44.528350   
...                       ...       ...       ...       ...        ...   
2023-08-02 23:55:00  6.136880  1.349454  4.275706  2.272397  21.724077   
2023-08-02 23:56:00  6.319551  4.138679  3.201096  3.311846  31.779905   
2023-08-02 23:57:00  6.337831  5.011087  1.963010  3.117730  29.610460   
2023-08-02 23:58:00  6.375566  5.301897 -0.116511  3.511872  33.463154   
2023-08-02 23:59:00  6.248019  5.524705 -0.014604  2.879642  27.457924   

                        phi_gse    bx_gsm    by_gsm    bz_gsm  theta_gsm  \
2021-01-01 00:00:00  244.252240 -0.909816 -1.917667  2.105494  44.755775   
2021-01-01 00:01:00  243.759570 -1.039568 -2.111495  1.821377  37.694405   
2021-01-01 00:02:00  244.819780 -1.012260 -2.130925  1.812792  37.482628   
2021-01-01 00:03:00  240.313740 -1.226179 -2.129280  1.619645  33.359356   
2021-01-01 00:04:00  237.794600 -1.335279 -2.124469  1.613821  32.711480   
...                         ...       ...       ...       ...        ...   
2023-08-02 23:55:00   72.550385  1.349454  4.502228  1.782157  16.762802   
2023-08-02 23

## Hour based

In [13]:
l1_sample_hour = l1_sample.resample('60min').mean()
#l1_sample_hour = (l1_sample[0].resample('60min').mean(), l1_sample[1].resample('60min').mean())
l1_sample_hour

proton_vx_gse  proton_vy_gse  proton_vz_gse  \
2021-01-01 00:00:00    -373.171990       2.683102      31.826852   
2021-01-01 01:00:00    -366.378726       7.539931      23.541713   
2021-01-01 02:00:00    -358.726689       2.736366      29.507315   
2021-01-01 03:00:00    -363.925997       0.668819      25.073611   
2021-01-01 04:00:00    -362.747894      -2.865486      37.946065   
...                            ...            ...            ...   
2023-08-02 19:00:00    -379.765862      25.943118     -16.354576   
2023-08-02 20:00:00    -376.328292      41.727040     -19.253179   
2023-08-02 21:00:00    -371.895862      38.995905     -19.274588   
2023-08-02 22:00:00    -367.047499      23.223777     -20.478057   
2023-08-02 23:00:00    -362.125494      17.855452     -25.700794   

                     proton_vx_gsm  proton_vy_gsm  proton_vz_gsm  \
2021-01-01 00:00:00    -373.171990      -5.216736      31.516250   
2021-01-01 01:00:00    -366.378726       2.030370      24.613356   
2021-01-01 02:00:00    -358.726689      -2.908148      29.499445   
2021-01-01 03:00:00    -363.925997      -3.181875      24.907662   
2021-01-01 04:00:00    -362.747894      -6.888032      37.396898   
...                            ...            ...            ...   
2023-08-02 19:00:00    -379.765862      22.884401     -20.436172   
2023-08-02 20:00:00    -376.328292      38.759995     -24.672901   
2023-08-02 21:00:00    -371.895862      36.537763     -23.618397   
2023-08-02 22:00:00    -367.047499      20.945639     -22.810471   
2023-08-02 23:00:00    -362.125494      14.988061     -27.459326   

                     proton_speed  proton_density  proton_temperature  \
2021-01-01 00:00:00    374.658310        3.951486        53976.156467   
2021-01-01 01:00:00    367.852755        3.131470        58800.502967   
2021-01-01 02:00:00    360.289790        3.767947        72193.270183   
2021-01-01 03:00:00    365.473958        3.369477        54466.296483   
2021-01-01 04:00:00    365.045163        3.399914        51079.092567   
...                           ...             ...                 ...   
2023-08-02 19:00:00    381.071297       11.639850        51746.351117   
2023-08-02 20:00:00    379.174312       11.017532        46973.598650   
2023-08-02 21:00:00    374.511539       11.234845        40941.005050   
2023-08-02 22:00:00    368.462264       10.358216        54048.541800   
2023-08-02 23:00:00    363.646042       11.507768        43601.685450   

                           bt    bx_gse    by_gse    bz_gse  theta_gse  \
2021-01-01 00:00:00  3.003368 -0.333842 -1.868589  1.581690  35.663654   
2021-01-01 01:00:00  2.914760  1.200702 -0.867253  1.723657  38.525516   
2021-01-01 02:00:00  2.811720  2.238337 -0.676501  0.822945  17.857510   
2021-01-01 03:00:00  2.830859  1.306669 -1.409024  0.681829  15.640870   
2021-01-01 04:00:00  2.637933  1.125380 -0.965849  0.081414  -1.996197   
...                       ...       ...       ...       ...        ...   
2023-08-02 19:00:00  3.661311  1.481688  1.909883 -2.437106 -42.108153   
2023-08-02 20:00:00  3.927160  2.266347  2.544638 -1.003132 -14.740523   
2023-08-02 21:00:00  4.408200  2.142368  3.082749  0.384495   4.364171   
2023-08-02 22:00:00  5.243963  4.217174  2.435149  0.514127   5.852604   
2023-08-02 23:00:00  5.333009  3.015120  2.495543  0.986613  10.948073   

                        phi_gse    bx_gsm    by_gsm    bz_gsm  theta_gsm  \
2021-01-01 00:00:00  262.106339 -0.333842 -2.203147  1.075751  22.859653   
2021-01-01 01:00:00  294.378127  1.200702 -1.229625  1.482598  32.110952   
2021-01-01 02:00:00  295.557833  2.238337 -0.817303  0.685229  14.625971   
2021-01-01 03:00:00  295.691196  1.306669 -1.509402  0.461889  10.126988   
2021-01-01 04:00:00  305.283648  1.125380 -0.994286 -0.023145  -5.680225   
...                         ...       ...       ...       ...        ...   
2023-08-02 19:00:00   54.782039  1.481688  1.484657 -2.722897 -48.649452   
2023-08-02 20

# L2 (cleaned) data

## Minute based

In [14]:
l2_sample

proton_vx_gse  proton_vy_gse  proton_vz_gse  \
2021-01-01 00:00:00         -375.4            5.3           33.7   
2021-01-01 00:01:00         -376.4            4.9           33.8   
2021-01-01 00:02:00         -375.7            4.3           36.7   
2021-01-01 00:03:00         -376.3            5.1           37.5   
2021-01-01 00:04:00         -377.8            5.0           34.7   
...                            ...            ...            ...   
2023-08-02 23:55:00         -354.6           19.7          -22.9   
2023-08-02 23:56:00         -350.3           13.9          -27.4   
2023-08-02 23:57:00         -356.6           20.5          -22.4   
2023-08-02 23:58:00         -352.5           12.5          -27.7   
2023-08-02 23:59:00         -352.7           10.4          -30.4   

                     proton_vx_gsm  proton_vy_gsm  proton_vz_gsm  \
2021-01-01 00:00:00         -375.4           -3.4           33.9   
2021-01-01 00:01:00         -376.4           -3.8           33.9   
2021-01-01 00:02:00         -375.7           -5.1           36.6   
2021-01-01 00:03:00         -376.3           -4.5           37.6   
2021-01-01 00:04:00         -377.8           -3.9           34.9   
...                            ...            ...            ...   
2023-08-02 23:55:00         -354.6           17.1          -25.0   
2023-08-02 23:56:00         -350.3           10.8          -28.8   
2023-08-02 23:57:00         -356.6           17.9          -24.5   
2023-08-02 23:58:00         -352.5            9.3          -28.9   
2023-08-02 23:59:00         -352.7            6.9          -31.3   

                     proton_speed  proton_density  proton_temperature    bt  \
2021-01-01 00:00:00         377.0            4.07             48945.0  3.03   
2021-01-01 00:01:00         377.9            4.14             48176.0  2.98   
2021-01-01 00:02:00         377.5            4.02             49682.0  2.99   
2021-01-01 00:03:00         378.2            4.00             48530.0  2.97   
2021-01-01 00:04:00         379.4            4.09             48764.0  3.00   
...                           ...             ...                 ...   ...   
2023-08-02 23:55:00         355.9           11.43             46133.0  6.16   
2023-08-02 23:56:00         351.7           10.01             38392.0  6.32   
2023-08-02 23:57:00         357.9           11.51             48911.0  6.34   
2023-08-02 23:58:00         353.8           10.53             44890.0  6.38   
2023-08-02 23:59:00         354.2           10.70             52269.0  6.25   

                     bx_gse  by_gse  bz_gse  theta_gse  phi_gse  bx_gsm  \
2021-01-01 00:00:00   -0.91   -1.35    2.52      57.23   236.02   -0.91   
2021-01-01 00:01:00   -1.04   -1.58    2.30      50.59   236.54   -1.04   
2021-01-01 00:02:00   -1.03   -1.62    2.28      49.90   237.48   -1.03   
2021-01-01 00:03:00   -1.25   -1.68    2.09      44.97   233.38   -1.25   
2021-01-01 00:04:00   -1.33   -1.65    2.11      44.95   231.12   -1.33   
...                     ...     ...     ...        ...      ...     ...   
2023-08-02 23:55:00    0.80    4.30    2.20      26.70    79.42    0.80   
2023-08-02 23:56:00    4.18    3.19    3.29      32.04    37.34    4.18   
2023-08-02 23:57:00    5.05    1.89    3.14      30.24    20.48    5.05   
2023-08-02 23:58:00    5.30   -0.08    3.48      33.29   359.16    5.30   
2023-08-02 23:59:00    5.53    0.00    2.86      27.38     0.00    5.53   

                     by_gsm  bz_gsm  theta_gsm  phi_gsm  
2021-01-01 00:00:00   -1.94    2.10      44.50   244.90  
2021-01-01 00:01:00   -2.10    1.83      37.93   243.66  
2021-01-01 00:02:00   -2.14    1.80      37.16   244.25  
2021-01-01 00:03:00   -2.15    1.60      32.79   239.86  
2021-01-01 00:04:00   -2.12    1.63      33.08   237.98  
...                     ...     ...        ...      ...  
2023-08-02 23:55:00    4.52    1.71      20.41    79.92  
2023-08-02 23:56:00    3.54    2.91      28.02    40.23  
2023-08-02 23:5

## Hour based

In [15]:
l2_sample_hour = l2_sample.resample('60min').mean()
#l2_sample_hour = (l2_sample[0].resample('60min').mean(), l2_sample[1].resample('60min').mean())
l2_sample_hour

proton_vx_gse  proton_vy_gse  proton_vz_gse  \
2021-01-01 00:00:00    -373.093333       2.780000      31.886667   
2021-01-01 01:00:00    -366.203333       7.566667      24.043333   
2021-01-01 02:00:00    -359.016667       2.728333      29.785000   
2021-01-01 03:00:00    -363.776667       0.763333      25.348333   
2021-01-01 04:00:00    -362.605000      -2.875000      38.110000   
...                            ...            ...            ...   
2023-08-02 19:00:00    -379.760000      25.843333     -16.345000   
2023-08-02 20:00:00    -376.306667      41.650000     -19.246667   
2023-08-02 21:00:00    -371.931667      39.231667     -19.265000   
2023-08-02 22:00:00    -367.041667      23.380000     -20.411667   
2023-08-02 23:00:00    -362.051667      18.056667     -25.765000   

                     proton_vx_gsm  proton_vy_gsm  proton_vz_gsm  \
2021-01-01 00:00:00    -373.093333      -5.140000      31.591667   
2021-01-01 01:00:00    -366.203333       1.946667      25.120000   
2021-01-01 02:00:00    -359.016667      -2.988333      29.770000   
2021-01-01 03:00:00    -363.776667      -3.136667      25.195000   
2021-01-01 04:00:00    -362.605000      -6.938333      37.546667   
...                            ...            ...            ...   
2023-08-02 19:00:00    -379.760000      22.786667     -20.411667   
2023-08-02 20:00:00    -376.306667      38.681667     -24.670000   
2023-08-02 21:00:00    -371.931667      36.780000     -23.646667   
2023-08-02 22:00:00    -367.041667      21.098333     -22.753333   
2023-08-02 23:00:00    -362.051667      15.185000     -27.541667   

                     proton_speed  proton_density  proton_temperature  \
2021-01-01 00:00:00    374.536667        3.946000        52724.916667   
2021-01-01 01:00:00    367.440000        3.117167        57286.500000   
2021-01-01 02:00:00    360.473333        3.835833        73188.833333   
2021-01-01 03:00:00    365.161667        3.357000        52968.000000   
2021-01-01 04:00:00    364.798333        3.386333        50097.416667   
...                           ...             ...                 ...   
2023-08-02 19:00:00    381.041667       11.615333        50594.700000   
2023-08-02 20:00:00    379.136667       10.993833        46535.050000   
2023-08-02 21:00:00    374.556667       11.230000        40499.733333   
2023-08-02 22:00:00    368.431667       10.335000        53604.400000   
2023-08-02 23:00:00    363.565000       11.485000        43130.366667   

                           bt    bx_gse    by_gse    bz_gse  theta_gse  \
2021-01-01 00:00:00  3.003667 -0.339000 -1.871000  1.585500  36.085500   
2021-01-01 01:00:00  2.915500  1.206167 -0.868833  1.731833  38.993333   
2021-01-01 02:00:00  2.812000  2.242000 -0.680000  0.820833  17.819833   
2021-01-01 03:00:00  2.833167  1.311333 -1.408167  0.683167  15.967000   
2021-01-01 04:00:00  2.639000  1.130167 -0.967500  0.080000  -2.054500   
...                       ...       ...       ...       ...        ...   
2023-08-02 19:00:00  3.661500  1.486333  1.911833 -2.440833 -42.267333   
2023-08-02 20:00:00  3.930500  2.268833  2.555500 -1.003833 -14.788000   
2023-08-02 21:00:00  4.421833  2.152833  3.104833  0.389167   4.441667   
2023-08-02 22:00:00  5.246167  4.233000  2.438667  0.504333   5.774000   
2023-08-02 23:00:00  5.335000  3.008333  2.511333  0.978833  11.023333   

                        phi_gse    bx_gsm    by_gsm    bz_gsm  theta_gsm  \
2021-01-01 00:00:00  254.077000 -0.339000 -2.206500  1.079000  23.017000   
2021-01-01 01:00:00  280.579333  1.206167 -1.233333  1.489833  32.416833   
2021-01-01 02:00:00  287.043000  2.242000 -0.820167  0.682000  14.558000   
2021-01-01 03:00:00  297.637833  1.311333 -1.509500  0.463500  10.307333   
2021-01-01 04:00:00  319.488500  1.130167 -0.995333 -0.025333  -5.797833   
...                         ...       ...       ...       ...        ...   
2023-08-02 19:00:00   52.338667  1.486333  1.485000 -2.726833 -48.841667   
2023-08-02 20

# Dst data

In [16]:
dst

0        -1
1        -2
2        -2
3        -3
4        -4
         ..
22651   -29
22652   -31
22653   -32
22654   -30
22655   -24
Name: Dst, Length: 22656, dtype: int64

# Kp data

In [17]:
kp

0        0
1       0+
2       1-
3       0+
4       0+
        ..
7547    3+
7548     4
7549    4-
7550     2
7551    2-
Name: Kp, Length: 7552, dtype: object

# Datasets
### Descriptions:
**hn_dl**: hour normal dataloader

**mn_dl**: minute normal dataloader

**hr_dl**: minute normal dataloader

**mr_dl**: minute normal dataloader



In [18]:
device = get_default_device()

In [19]:
sequence_length_hour = 10  #hour
sequence_length_minute = 600 #minute
pred_length = 9 #hours

In [20]:
##Normal
hour_Normal_dataset = NormalTrainingDataset(l1_sample_hour, dst, kp, sequence_length_hour, pred_length, hour = True)
minute_Normal_dataset = NormalTrainingDataset(l1_sample, dst, kp, sequence_length_minute, pred_length, hour = False)
##Refined(new method)
hour_Refined_dataset = RefinedTrainingDataset(l1_sample_hour, l2_sample_hour, dst,kp,sequence_length_hour, pred_length, hour = True)
minute_Refined_dataset = RefinedTrainingDataset(l1_sample, l2_sample, dst,kp,sequence_length_minute, pred_length, hour = False)

In [21]:
for i,(feature, dst, kp) in enumerate(hour_Normal_dataset):
    print(feature.size())
    print(dst.size())
    print(kp.size())
    print(i.size())


tensor([[ 0.6947, -0.2811,  0.8946,  0.6947, -0.4846,  0.9092, -0.7058, -0.8674,
         -0.6802, -1.0359, -0.1740, -0.4173,  0.5256,  1.3772,  0.7109, -0.1740,
         -0.5139,  0.3680,  0.8780,  0.7154],
        [ 0.7772, -0.1330,  0.6567,  0.7772, -0.2686,  0.7084, -0.7872, -1.0368,
         -0.6555, -1.0666,  0.2727, -0.1642,  0.5733,  1.4863,  1.0919,  0.2727,
         -0.2615,  0.4990,  1.2113,  1.0995],
        [ 0.8702, -0.2795,  0.8280,  0.8702, -0.4158,  0.8505, -0.8776, -0.9053,
         -0.5869, -1.1024,  0.5748, -0.1160,  0.2709,  0.6985,  1.1058,  0.5748,
         -0.1546,  0.2422,  0.5814,  1.1135],
        [ 0.8070, -0.3426,  0.7007,  0.8070, -0.4240,  0.7170, -0.8156, -0.9876,
         -0.6777, -1.0958,  0.3035, -0.3011,  0.2235,  0.6140,  1.1074,  0.3035,
         -0.3341,  0.1703,  0.4194,  1.1151],
        [ 0.8213, -0.4504,  1.0703,  0.8213, -0.5345,  1.0802, -0.8208, -0.9814,
         -0.6950, -1.1628,  0.2508, -0.1891,  0.0219, -0.0582,  1.2206,  0.2508,
      

KeyboardInterrupt: 

In [16]:
###Extra dataset
hour_kp_dataset = MainToSingleTarget(l1_sample, kp, sequence_length_hour, pred_length, hour = True, sep = True, target_mode='kp_gfz')
minute_kp_dataset = MainToSingleTarget(l1_sample, kp, sequence_length_minute, pred_length, hour = False, sep = True, target_mode='kp_gfz')

In [17]:
#Test:5% training: 95%

test_size = round(0.05*len(hour_kp_dataset))

train_hour_kp, test_hour_kp = random_split(hour_kp_dataset , [len(hour_kp_dataset) - test_size, test_size])

batch_size = 32  #Change based on GPU capacity

train_hour_kp_dl = DataLoader(train_hour_kp, batch_size, shuffle=True, num_workers=4, pin_memory=True)
train_hour_kp_dl = DeviceDataLoader(train_hour_kp_dl, device)
test_hour_kp_dl = DataLoader(test_hour_kp, batch_size*2, num_workers=4, pin_memory=True)
test_hour_kp_dl = DeviceDataLoader(test_hour_kp_dl, device)

In [18]:
#Test:5% training: 95%

test_size = round(0.05*len(minute_kp_dataset))

train_minute_kp, test_minute_kp = random_split(minute_kp_dataset , [len(minute_kp_dataset) - test_size, test_size])

batch_size = 32  #Change based on GPU capacity

train_minute_kp_dl = DataLoader(train_minute_kp, batch_size, shuffle=True, num_workers=4, pin_memory=True)
train_minute_kp_dl = DeviceDataLoader(train_minute_kp_dl, device)
test_minute_kp_dl = DataLoader(test_minute_kp, batch_size*2, num_workers=4, pin_memory=True)
test_minute_kp_dl = DeviceDataLoader(test_minute_kp_dl, device)

In [36]:
#Test:5% training: 95%

test_size = round(0.05*len(hour_Normal_dataset))

train_hn_ds, test_hn_ds = random_split(hour_Normal_dataset , [len(hour_Normal_dataset) - test_size, test_size])

batch_size = 32  #Change based on GPU capacity

train_hn_dl = DataLoader(train_hn_ds, batch_size, shuffle=True, num_workers=4, pin_memory=True)
train_hn_dl = DeviceDataLoader(train_hn_dl, device)
test_hn_dl = DataLoader(test_hn_ds, batch_size*2, num_workers=4, pin_memory=True)
test_hn_dl = DeviceDataLoader(test_hn_dl, device)

In [37]:
#Test:5% training: 95%

test_size = round(0.05*len(minute_Normal_dataset))

train_mn_ds, test_mn_ds = random_split(minute_Normal_dataset , [len(minute_Normal_dataset) - test_size, test_size])

batch_size = 32  #Change based on GPU capacity

train_mn_dl = DataLoader(train_mn_ds, batch_size, shuffle=True, num_workers=4, pin_memory=True)
train_mn_dl = DeviceDataLoader(train_mn_dl, device)
test_mn_dl = DataLoader(test_mn_ds, batch_size*2, num_workers=4, pin_memory=True)
test_mn_dl = DeviceDataLoader(test_mn_dl, device)


In [38]:
#Test:5% training: 95%

test_size = round(0.05*len(hour_Refined_dataset))

train_hr_ds, test_hr_ds = random_split(hour_Refined_dataset , [len(hour_Refined_dataset) - test_size, test_size])

batch_size = 32  #Change based on GPU capacity

train_hr_dl = DataLoader(train_hr_ds, batch_size, shuffle=True, num_workers=4, pin_memory=True)
train_hr_dl = DeviceDataLoader(train_hr_dl, device)
test_hr_dl = DataLoader(test_hr_ds, batch_size*2, num_workers=4, pin_memory=True)
test_hr_dl = DeviceDataLoader(test_hr_dl, device)

In [39]:
#Test:5% training: 95%

test_size = round(0.05*len(minute_Refined_dataset))

train_mr_ds, test_mr_ds = random_split(minute_Refined_dataset , [len(minute_Refined_dataset) - test_size, test_size])

batch_size = 32  #Change based on GPU capacity

train_mr_dl = DataLoader(train_mr_ds, batch_size, shuffle=True, num_workers=4, pin_memory=True)
train_mr_dl = DeviceDataLoader(train_mr_dl, device)
test_mr_dl = DataLoader(test_mr_ds, batch_size*2, num_workers=4, pin_memory=True)
test_mr_dl = DeviceDataLoader(test_mr_dl, device)

# Models

## Refined models with attention

### 1d Convolutional encoder

In [19]:
## Architecture
hidden_size = 10
input_size = 20
##nn architecture
architecture = ()

In [ ]:
#encoders
cnn_encoder_min = Simple1DCNN(architecture, sequence_length_minute, hidden_size)
cnn_encoder_hour = Simple1DCNN(architecture, sequence_length_hour, hidden_size)
#fc layer
cnn_fc_dst_min = DeepNeuralNetwork(hidden_size, pred_length, *architecture)
cnn_fc_kp_min = DeepNeuralNetwork(hidden_size, hour_to_3_hour(pred_length), *architecture)

cnn_fc_dst_hour = DeepNeuralNetwork(hidden_size, pred_length, *architecture)
cnn_fc_kp_hour = DeepNeuralNetwork(hidden_size, hour_to_3_hour(pred_length), *architecture)

In [ ]:
RefinedCNN_min = to_device(RefinedArchitecture(cnn_encoder_min, cnn_fc_dst_min, cnn_fc_kp_min), device)
RefinedCNN_hour = to_device(RefinedArchitecture(cnn_encoder_hour, cnn_fc_dst_hour, cnn_fc_kp_hour), device)

In [ ]:
##hyperparameters
epochs = 20
max_lr = 1e-2
weigth_decay = 1e-6
grad_clip = 1e-1
opt_func = Adam
#opt_func = RMSprop

In [ ]:
RefinedCNN_min_history = []

In [ ]:
RefinedCNN_min_history += RefinedCNN_min.fit(epochs, max_lr, train_mr_dl, test_mr_dl, weigth_decay, grad_clip, opt_func)

Epoch [0]
	last_lr: 0.00005
	train_overall_loss: 1.2622
	train_main_loss: 1.2621
	train_output_loss: 0.0028
	train_encoder_loss: 0.0038
	val_overall_loss: 1.1528
	val_main_loss: 1.1527
	val_output_loss: 0.0040
	val_encoder_loss: 0.0065
Epoch [1]
	last_lr: 0.00014
	train_overall_loss: 1.1290
	train_main_loss: 1.1288
	train_output_loss: 0.0039
	train_encoder_loss: 0.0233
	val_overall_loss: 1.1327
	val_main_loss: 1.1319
	val_output_loss: 0.0054
	val_encoder_loss: 0.0798
Epoch [2]
	last_lr: 0.00026
	train_overall_loss: 1.1277
	train_main_loss: 1.1256
	train_output_loss: 0.0042
	train_encoder_loss: 0.2093
	val_overall_loss: 1.1478
	val_main_loss: 1.1448
	val_output_loss: 0.0051
	val_encoder_loss: 0.2883


KeyboardInterrupt: 

In [ ]:
RefinedCNN_hour_history = []

In [ ]:
RefinedCNN_hour_history += RefinedCNN_hour.fit(epochs, max_lr, train_hr_dl, test_hr_dl, weigth_decay, grad_clip, opt_func)

Epoch [0]
	last_lr: 0.00104
	train_overall_loss: 1.2932
	train_main_loss: 1.2931
	train_output_loss: 0.0021
	train_encoder_loss: 0.0009
	val_overall_loss: 1.2866
	val_main_loss: 1.2865
	val_output_loss: 0.0017
	val_encoder_loss: 0.0008
Epoch [1]
	last_lr: 0.00280
	train_overall_loss: 1.2405
	train_main_loss: 1.2405
	train_output_loss: 0.0030
	train_encoder_loss: 0.0011
	val_overall_loss: 1.2383
	val_main_loss: 1.2383
	val_output_loss: 0.0020
	val_encoder_loss: 0.0010
Epoch [2]
	last_lr: 0.00520
	train_overall_loss: 1.2127
	train_main_loss: 1.2127
	train_output_loss: 0.0034
	train_encoder_loss: 0.0014
	val_overall_loss: 1.2170
	val_main_loss: 1.2169
	val_output_loss: 0.0024
	val_encoder_loss: 0.0014
Epoch [3]
	last_lr: 0.00760
	train_overall_loss: 1.2079
	train_main_loss: 1.2078
	train_output_loss: 0.0032
	train_encoder_loss: 0.0019
	val_overall_loss: 1.2843
	val_main_loss: 1.2843
	val_output_loss: 0.0035
	val_encoder_loss: 0.0024
Epoch [4]
	last_lr: 0.00936
	train_overall_loss: 1.1980


KeyboardInterrupt: 

### Bidirectional Deep LSTM encoder

In [41]:
## Architecture
hidden_size = 10
input_size = 20
##nn architecture
architecture = ()

In [42]:
#encoders
##Bidirectional minute based models
deep_lstm_encoder_min_forward = DeepLSTM(hidden_size, input_size, architecture, attention = True).to(device)
deep_lstm_encoder_min_backward = DeepLSTM(hidden_size, input_size, architecture, attention = True).to(device)
bidirectional_deeplstm_encoder_min = BidirectionalRNN(deep_lstm_encoder_min_forward, deep_lstm_encoder_min_backward).to(device)
##Bidirectional hour based models
deep_lstm_encoder_hour_forward = DeepLSTM(hidden_size, input_size, architecture, attention = True).to(device)
deep_lstm_encoder_hour_backward = DeepLSTM(hidden_size, input_size, architecture, attention = True).to(device)
bidirectional_deeplstm_encoder_hour = BidirectionalRNN(deep_lstm_encoder_hour_forward, deep_lstm_encoder_hour_backward).to(device)
#fc layer
deep_lstm_fc_dst_min = DeepNeuralNetwork(2*hidden_size, pred_length, *architecture).to(device) #the multiplying factor because concatenating hidden_states on bidirectional arch
deep_lstm_fc_kp_min = DeepNeuralNetwork(2*hidden_size, hour_to_3_hour(pred_length), *architecture).to(device)

deep_lstm_fc_dst_hour = DeepNeuralNetwork(2*hidden_size, pred_length, *architecture).to(device)
deep_lstm_fc_kp_hour = DeepNeuralNetwork(2*hidden_size, hour_to_3_hour(pred_length), *architecture).to(device)

In [43]:
RefinedLSTM_min = to_device(RefinedArchitecture(bidirectional_deeplstm_encoder_min, deep_lstm_fc_dst_min, deep_lstm_fc_kp_min), device)
RefinedLSTM_hour = to_device(RefinedArchitecture(bidirectional_deeplstm_encoder_hour, deep_lstm_fc_dst_hour, deep_lstm_fc_kp_hour), device)

In [44]:
##hyperparameters
epochs = 10
max_lr = 1e-2
weigth_decay = 1e-3
grad_clip = 1e-1
opt_func = Adam
#opt_func = RMSprop

In [ ]:
RefinedLSTM_min_history = []

In [ ]:
RefinedLSTM_min_history += RefinedLSTM_min.fit(epochs, max_lr, train_mr_dl, test_mr_dl, weigth_decay, grad_clip, opt_func)

RuntimeError: Expected all tensors to be on the same device, but found at least two devices, cuda:0 and cpu! (when checking argument for argument mat1 in method wrapper_CUDA_addmm)

In [45]:
RefinedLSTM_hour_history = []

In [46]:
RefinedLSTM_hour_history += RefinedLSTM_hour.fit(epochs, max_lr, train_hr_dl, test_hr_dl, weigth_decay, grad_clip, opt_func)

RuntimeError: Expected all tensors to be on the same device, but found at least two devices, cuda:0 and cpu! (when checking argument for argument mat1 in method wrapper_CUDA_addmm)

### Bidirectional Deep GRU encoder

In [ ]:
## Architecture
hidden_size = 10
input_size = 20
##nn architecture
architecture = ()

In [ ]:
#encoders
##Bidirectional minute based models
deep_gru_encoder_min_forward= DeepGRU(hidden_size, input_size, architecture)
deep_gru_encoder_min_backward= DeepGRU(hidden_size, input_size, architecture)
bidirectional_deepgru_encoder_min = BidirectionalRNN(deep_gru_encoder_min_forward, deep_gru_encoder_min_backward)
##Bidirectional hour based models
deep_gru_encoder_hour_forward = DeepGRU(hidden_size, input_size, architecture)
deep_gru_encoder_hour_backward = DeepGRU(hidden_size, input_size, architecture)
bidirectional_deepgru_encoder_hour = BidirectionalRNN(deep_gru_encoder_hour_forward, deep_gru_encoder_hour_backward)
#fc layer
deep_gru_fc_dst_min = DeepNeuralNetwork(2*hidden_size, pred_length, *architecture)
deep_gru_fc_kp_min = DeepNeuralNetwork(2*hidden_size, hour_to_3_hour(pred_length), *architecture)

deep_gru_fc_dst_hour = DeepNeuralNetwork(2*hidden_size, pred_length, *architecture)
deep_gru_fc_kp_hour = DeepNeuralNetwork(2*hidden_size, hour_to_3_hour(pred_length), *architecture)

In [ ]:
RefinedGRU_min = to_device(RefinedArchitecture(bidirectional_deepgru_encoder_min, deep_gru_fc_dst_min, deep_gru_fc_kp_min), device)
RefinedGRU_hour = to_device(RefinedArchitecture(bidirectional_deepgru_encoder_hour, deep_gru_fc_dst_hour, deep_gru_fc_kp_hour), device)

In [ ]:
##hyperparameters
epochs = 100
max_lr = 1e-2
weigth_decay = 1e-6
grad_clip = 5e-1
opt_func = Adam
#opt_func = RMSprop

In [ ]:
RefinedGRU_min_history = []

In [ ]:
RefinedGRU_min_history += RefinedGRU_min.fit(epochs, max_lr, train_mr_dl, test_mr_dl, weigth_decay, grad_clip, opt_func)

In [ ]:
RefinedGRU_hour_history = []

In [ ]:
RefinedGRU_hour_history += RefinedGRU_hour.fit(epochs, max_lr, train_hr_dl, test_hr_dl, weigth_decay, grad_clip, opt_func)

NameError: name 'RefinedGRU_hour_history' is not defined

### Bidirectional Deep Vanilla RNN encoder

In [ ]:
## Architecture
hidden_size = 10
input_size = 20
##nn architecture
architecture = ()

In [ ]:
#encoders
##Bidirectional minute encoders
deep_rnn_encoder_min_forward = DeepVanillaRNN(hidden_size, input_size, architecture)
deep_rnn_encoder_min_backward = DeepVanillaRNN(hidden_size, input_size, architecture)
bidirectional_deeprnn_encoder_min = BidirectionalRNN(deep_rnn_encoder_min_forward,deep_rnn_encoder_min_backward)
##Bidirectional hour encoders
deep_rnn_encoder_hour_forward = DeepVanillaRNN(hidden_size, input_size, architecture)
deep_rnn_encoder_hour_backward = DeepVanillaRNN(hidden_size, input_size, architecture)
bidirectional_deeprnn_encoder_hour = BidirectionalRNN(deep_rnn_encoder_hour_forward,deep_rnn_encoder_hour_backward)
#fc layer
deep_rnn_fc_dst_min = DeepNeuralNetwork(2*hidden_size, pred_length, *architecture)
deep_rnn_fc_kp_min = DeepNeuralNetwork(2*hidden_size, hour_to_3_hour(pred_length), *architecture)

deep_rnn_fc_dst_hour = DeepNeuralNetwork(2*hidden_size, pred_length, *architecture)
deep_rnn_fc_kp_hour = DeepNeuralNetwork(2*hidden_size, hour_to_3_hour(pred_length), *architecture)

In [ ]:
RefinedVanillaRNN_min = to_device(RefinedArchitecture(bidirectional_deeprnn_encoder_min, deep_rnn_fc_dst_min, deep_rnn_fc_kp_min), device)
RefinedVanillaRNN_hour = to_device(RefinedArchitecture(bidirectional_deeprnn_encoder_hour, deep_rnn_fc_dst_hour, deep_rnn_fc_kp_hour), device)

In [ ]:
##hyperparameters
epochs = 100
max_lr = 1e-3
weigth_decay = 1e-4
grad_clip = 1e-2
#opt_func = Adam
opt_func = RMSprop

In [ ]:
RefinedVanillaRNN_min_history = []

In [ ]:
RefinedVanillaRNN_min_history += RefinedVanillaRNN_min.fit(epochs, max_lr, train_mr_dl, test_mr_dl, weigth_decay, grad_clip, opt_func)

In [ ]:
RefinedVanillaRNN_hour_history = []

In [ ]:
RefinedVanillaRNN_hour_history += RefinedVanillaRNN_hour.fit(epochs, max_lr, train_hr_dl, test_hr_dl, weigth_decay, grad_clip, opt_func)

Epoch [0]
	last_lr: 0.00004
	train_overall_loss: 1.3494
	train_main_loss: 1.3494
	train_output_loss: 0.0001
	train_encoder_loss: 0.0001
	val_overall_loss: 1.2106
	val_main_loss: 1.2106
	val_output_loss: 0.0002
	val_encoder_loss: 0.0001
Epoch [1]
	last_lr: 0.00005
	train_overall_loss: 1.0410
	train_main_loss: 1.0410
	train_output_loss: 0.0003
	train_encoder_loss: 0.0001
	val_overall_loss: 1.0773
	val_main_loss: 1.0773
	val_output_loss: 0.0004
	val_encoder_loss: 0.0001


KeyboardInterrupt: 

### Bidirectional non deep architectures

#### LSTM

In [ ]:
non_deep_lstm_forward_min = LSTM(input_size, hidden_size)
non_deep_lstm_backward_min = LSTM(input_size, hidden_size)
bidirectional_lstm_encoder_min = BidirectionalRNNWithAttention(non_deep_lstm_forward_min, non_deep_lstm_backward_min)

non_deep_lstm_forward_hour = LSTM(input_size, hidden_size)
non_deep_lstm_backward_hour = LSTM(input_size, hidden_size)
bidirectional_lstm_encoder_hour = BidirectionalRNNWithAttention(non_deep_lstm_forward_hour, non_deep_lstm_backward_hour)
#fc layer
non_deep_lstm_fc_dst_min = DeepNeuralNetwork(2*hidden_size, pred_length, *architecture)
non_deep_lstm_fc_kp_min = DeepNeuralNetwork(2*hidden_size, hour_to_3_hour(pred_length), *architecture)

non_deep_lstm_fc_dst_hour = DeepNeuralNetwork(2*hidden_size, pred_length, *architecture)
non_deep_lstm_fc_kp_hour = DeepNeuralNetwork(2*hidden_size, hour_to_3_hour(pred_length), *architecture)

In [ ]:
RefinedNonDeepLSTM_min = to_device(RefinedArchitecture(bidirectional_lstm_encoder_min, non_deep_lstm_fc_dst_min, non_deep_lstm_fc_kp_min), device)
RefinedNonDeepLSTM_hour = to_device(RefinedArchitecture(bidirectional_lstm_encoder_hour, non_deep_lstm_fc_dst_hour, non_deep_lstm_fc_kp_hour), device)

In [ ]:
RefinedNonDeepLSTM_min_history = []

In [ ]:
RefinedNonDeepLSTM_min_history += RefinedNonDeepLSTM_min.fit(epochs, max_lr, train_mr_dl, test_mr_dl, weigth_decay, grad_clip, opt_func)

In [ ]:
RefinedNonDeepLSTM_hour_history = []

In [ ]:
RefinedNonDeepLSTM_hour_history += RefinedNonDeepLSTM_hour.fit(epochs, max_lr, train_hr_dl, test_hr_dl, weigth_decay, grad_clip, opt_func)

Epoch [0]
	last_lr: 0.00004
	train_overall_loss: 1.3338
	train_main_loss: 1.3338
	train_output_loss: 0.0002
	train_encoder_loss: 0.0001
	val_overall_loss: 1.1319
	val_main_loss: 1.1319
	val_output_loss: 0.0004
	val_encoder_loss: 0.0001
Epoch [1]
	last_lr: 0.00005
	train_overall_loss: 0.9605
	train_main_loss: 0.9605
	train_output_loss: 0.0005
	train_encoder_loss: 0.0001
	val_overall_loss: 0.9760
	val_main_loss: 0.9760
	val_output_loss: 0.0005
	val_encoder_loss: 0.0001
Epoch [2]
	last_lr: 0.00006
	train_overall_loss: 0.8491
	train_main_loss: 0.8491
	train_output_loss: 0.0008
	train_encoder_loss: 0.0002
	val_overall_loss: 0.8663
	val_main_loss: 0.8663
	val_output_loss: 0.0005
	val_encoder_loss: 0.0001
Epoch [3]
	last_lr: 0.00008
	train_overall_loss: 0.7699
	train_main_loss: 0.7698
	train_output_loss: 0.0008
	train_encoder_loss: 0.0002
	val_overall_loss: 0.7792
	val_main_loss: 0.7792
	val_output_loss: 0.0006
	val_encoder_loss: 0.0002
Epoch [4]
	last_lr: 0.00010
	train_overall_loss: 0.7140


KeyboardInterrupt: 

#### GRU

In [ ]:
non_deep_gru_forward_min = GRU(input_size, hidden_size)
non_deep_gru_backward_min = GRU(input_size, hidden_size)
bidirectional_gru_encoder_min = BidirectionalRNNWithAttention(non_deep_gru_forward_min, non_deep_gru_backward_min)

non_deep_gru_forward_hour = GRU(input_size, hidden_size)
non_deep_gru_backward_hour = GRU(input_size, hidden_size)
bidirectional_gru_encoder_hour = BidirectionalRNNWithAttention(non_deep_gru_forward_hour, non_deep_gru_backward_hour)
#fc layer
non_deep_gru_fc_dst_min = DeepNeuralNetwork(2*hidden_size, pred_length, *architecture)
non_deep_gru_fc_kp_min = DeepNeuralNetwork(2*hidden_size, hour_to_3_hour(pred_length), *architecture)

non_deep_gru_fc_dst_hour = DeepNeuralNetwork(2*hidden_size, pred_length, *architecture)
non_deep_gru_fc_kp_hour = DeepNeuralNetwork(2*hidden_size, hour_to_3_hour(pred_length), *architecture)


In [ ]:
RefinedNonDeepGRU_min = to_device(RefinedArchitecture(bidirectional_gru_encoder_min, non_deep_gru_fc_dst_min, non_deep_gru_fc_kp_min), device)
RefinedNonDeepGRU_hour = to_device(RefinedArchitecture(bidirectional_gru_encoder_hour, non_deep_gru_fc_dst_hour, non_deep_gru_fc_kp_hour), device)

In [ ]:
RefinedNonDeepGRU_min_history = []

In [ ]:
RefinedNonDeepGRU_min_history += RefinedNonDeepGRU_min.fit(epochs, max_lr, train_mr_dl, test_mr_dl, weigth_decay, grad_clip, opt_func)

In [ ]:
RefinedNonDeepGRU_hour_history = []

In [ ]:
RefinedNonDeepGRU_hour_history += RefinedNonDeepGRU_hour.fit(epochs, max_lr, train_hr_dl, test_hr_dl, weigth_decay, grad_clip, opt_func)

Epoch [0]
	last_lr: 0.00004
	train_overall_loss: 1.3516
	train_main_loss: 1.3516
	train_output_loss: 0.0002
	train_encoder_loss: 0.0001
	val_overall_loss: 1.1860
	val_main_loss: 1.1860
	val_output_loss: 0.0003
	val_encoder_loss: 0.0001
Epoch [1]
	last_lr: 0.00005
	train_overall_loss: 0.9823
	train_main_loss: 0.9823
	train_output_loss: 0.0003
	train_encoder_loss: 0.0001
	val_overall_loss: 1.0192
	val_main_loss: 1.0192
	val_output_loss: 0.0005
	val_encoder_loss: 0.0001
Epoch [2]
	last_lr: 0.00006
	train_overall_loss: 0.8637
	train_main_loss: 0.8637
	train_output_loss: 0.0005
	train_encoder_loss: 0.0001
	val_overall_loss: 0.9084
	val_main_loss: 0.9084
	val_output_loss: 0.0005
	val_encoder_loss: 0.0001
Epoch [3]
	last_lr: 0.00008
	train_overall_loss: 0.7905
	train_main_loss: 0.7905
	train_output_loss: 0.0005
	train_encoder_loss: 0.0001
	val_overall_loss: 0.8263
	val_main_loss: 0.8263
	val_output_loss: 0.0005
	val_encoder_loss: 0.0001
Epoch [4]
	last_lr: 0.00010
	train_overall_loss: 0.7357


KeyboardInterrupt: 

#### RNN

In [ ]:
non_deep_rnn_forward_min = VanillaRNN(input_size, hidden_size)
non_deep_rnn_backward_min = VanillaRNN(input_size, hidden_size)
bidirectional_rnn_encoder_min = BidirectionalRNNWithAttention(non_deep_rnn_forward_min, non_deep_rnn_backward_min)

non_deep_rnn_forward_hour = VanillaRNN(input_size, hidden_size)
non_deep_rnn_backward_hour = VanillaRNN(input_size, hidden_size)
bidirectional_rnn_encoder_hour = BidirectionalRNNWithAttention(non_deep_rnn_forward_hour, non_deep_rnn_backward_hour)
#fc layer
non_deep_rnn_fc_dst_min = DeepNeuralNetwork(2*hidden_size, pred_length, *architecture)
non_deep_rnn_fc_kp_min = DeepNeuralNetwork(2*hidden_size, hour_to_3_hour(pred_length), *architecture)

non_deep_rnn_fc_dst_hour = DeepNeuralNetwork(2*hidden_size, pred_length, *architecture)
non_deep_rnn_fc_kp_hour = DeepNeuralNetwork(2*hidden_size, hour_to_3_hour(pred_length), *architecture)


In [ ]:
RefinedNonDeepVanillaRNN_min = to_device(RefinedArchitecture(bidirectional_rnn_encoder_min, non_deep_rnn_fc_dst_min, non_deep_rnn_fc_kp_min), device)
RefinedNonDeepVanillaRNN_hour = to_device(RefinedArchitecture(bidirectional_rnn_encoder_hour, non_deep_rnn_fc_dst_hour, non_deep_rnn_fc_kp_hour), device)

In [ ]:
RefinedNonDeepVanillaRNN_min_history = []

In [ ]:
RefinedNonDeepVanillaRNN_min_history += RefinedNonDeepVanillaRNN_min.fit(epochs, max_lr, train_mr_dl, test_mr_dl, weigth_decay, grad_clip, opt_func)

In [ ]:
RefinedNonDeepVanillaRNN_hour_history = []

In [ ]:
RefinedNonDeepVanillaRNN_hour_history += RefinedNonDeepVanillaRNN_hour.fit(epochs, max_lr, train_hr_dl, test_hr_dl, weigth_decay, grad_clip, opt_func)

Epoch [0]
	last_lr: 0.00004
	train_overall_loss: 1.2946
	train_main_loss: 1.2946
	train_output_loss: 0.0002
	train_encoder_loss: 0.0002
	val_overall_loss: 1.1871
	val_main_loss: 1.1871
	val_output_loss: 0.0003
	val_encoder_loss: 0.0002
Epoch [1]
	last_lr: 0.00005
	train_overall_loss: 1.0257
	train_main_loss: 1.0257
	train_output_loss: 0.0003
	train_encoder_loss: 0.0002
	val_overall_loss: 1.0831
	val_main_loss: 1.0830
	val_output_loss: 0.0005
	val_encoder_loss: 0.0002
Epoch [2]
	last_lr: 0.00006
	train_overall_loss: 0.9554
	train_main_loss: 0.9554
	train_output_loss: 0.0005
	train_encoder_loss: 0.0002
	val_overall_loss: 1.0201
	val_main_loss: 1.0201
	val_output_loss: 0.0006
	val_encoder_loss: 0.0002


KeyboardInterrupt: 

## Normal models with attention

### 1d Convolutional encoder

In [ ]:
## Architecture
hidden_size = 10
input_size = 20
##nn architecture
architecture = ()

In [ ]:
#encoders
cnn_encoder_min = Simple1DCNN(architecture, input_size, hidden_size)
cnn_encoder_hour = Simple1DCNN(architecture, input_size, hidden_size)
#fc layer
cnn_fc_dst_min = DeepNeuralNetwork(hidden_size, pred_length, *architecture)
cnn_fc_kp_min = DeepNeuralNetwork(hidden_size, hour_to_3_hour(pred_length), *architecture)

cnn_fc_dst_hour = DeepNeuralNetwork(hidden_size, pred_length, *architecture)
cnn_fc_kp_hour = DeepNeuralNetwork(hidden_size, hour_to_3_hour(pred_length), *architecture)

In [ ]:
NormalCNN_min = to_device(NormalArchitecture(cnn_encoder_min, cnn_fc_dst_min, cnn_fc_kp_min), device)
NormalCNN_hour = to_device(NormalArchitecture(cnn_encoder_hour, cnn_fc_dst_hour, cnn_fc_kp_hour), device)

In [ ]:
##hyperparameters
epochs = 100
max_lr = 1e-3
weigth_decay = 1e-4
grad_clip = 1e-2
#opt_func = Adam
opt_func = RMSprop

In [ ]:
NormalCNN_min_history = []

In [ ]:
NormalCNN_min_history += NormalCNN_min.fit(epochs, max_lr, train_mn_dl, test_mn_dl, weigth_decay, grad_clip, opt_func)

In [ ]:
NormalCNN_hour_history = []

In [ ]:
NormalCNN_hour_history += NormalCNN_hour.fit(epochs, max_lr, train_hn_dl, test_hn_dl, weigth_decay, grad_clip, opt_func)

RuntimeError: Given groups=1, weight of size [10, 20, 3], expected input[32, 10, 20] to have 20 channels, but got 10 channels instead

### Bidirectional Deep LSTM encoder

In [ ]:
## Architecture
hidden_size = 10
input_size = 20
##nn architecture
architecture = ()

In [ ]:
#encoders
deep_lstm_encoder_min_forward = DeepLSTM(hidden_size, input_size, architecture)
deep_lstm_encoder_min_backward = DeepLSTM(hidden_size, input_size, architecture)
deep_lstm_encoder_min = BidirectionalRNNWithAttention(deep_lstm_encoder_min_forward,deep_lstm_encoder_min_backward)

deep_lstm_encoder_hour_forward = DeepLSTM(hidden_size, input_size, architecture)
deep_lstm_encoder_hour_backward = DeepLSTM(hidden_size, input_size, architecture)
deep_lstm_encoder_hour = BidirectionalRNNWithAttention(deep_lstm_encoder_hour_forward,deep_lstm_encoder_hour_backward)

#fc layer
deep_lstm_fc_dst_min = DeepNeuralNetwork(2*hidden_size, pred_length, *architecture)
deep_lstm_fc_kp_min = DeepNeuralNetwork(2*hidden_size, hour_to_3_hour(pred_length), *architecture)

deep_lstm_fc_dst_hour = DeepNeuralNetwork(2*hidden_size, pred_length, *architecture)
deep_lstm_fc_kp_hour = DeepNeuralNetwork(2*hidden_size, hour_to_3_hour(pred_length), *architecture)

In [ ]:
NormalLSTM_min = to_device(NormalArchitecture(deep_lstm_encoder_min, deep_lstm_fc_dst_min, deep_lstm_fc_kp_min), device)
NormalLSTM_hour = to_device(NormalArchitecture(deep_lstm_encoder_hour, deep_lstm_fc_dst_hour, deep_lstm_fc_kp_hour), device)

In [ ]:
##hyperparameters
epochs = 100
max_lr = 1e-3
weigth_decay = 1e-4
grad_clip = 1e-2
#opt_func = Adam
opt_func = RMSprop

In [ ]:
NormalLSTM_min_history = []

In [ ]:
NormalLSTM_min_history += NormalLSTM_min.fit(epochs, max_lr, train_mn_dl, test_mn_dl, weigth_decay, grad_clip, opt_func)

In [ ]:
NormalLSTM_hour_history = []

In [ ]:
NormalLSTM_hour_history += NormalLSTM_hour.fit(epochs, max_lr, train_hn_dl, test_hn_dl, weigth_decay, grad_clip, opt_func)

Epoch [0]:
	last_lr: 0.00004
	train_loss: 1.3096
	val_loss: 0.9849
Epoch [1]:
	last_lr: 0.00005
	train_loss: 0.9692
	val_loss: 0.8660
Epoch [2]:
	last_lr: 0.00006
	train_loss: 0.8529
	val_loss: 0.7863
Epoch [3]:
	last_lr: 0.00008
	train_loss: 0.7619
	val_loss: 0.7326
Epoch [4]:
	last_lr: 0.00010
	train_loss: 0.7028
	val_loss: 0.6870
Epoch [5]:
	last_lr: 0.00013
	train_loss: 0.6619
	val_loss: 0.6704
Epoch [6]:
	last_lr: 0.00016
	train_loss: 0.6341
	val_loss: 0.6449
Epoch [7]:
	last_lr: 0.00020
	train_loss: 0.6039
	val_loss: 0.6322
Epoch [8]:
	last_lr: 0.00024
	train_loss: 0.5860
	val_loss: 0.6194
Epoch [9]:
	last_lr: 0.00028
	train_loss: 0.5695
	val_loss: 0.5994


KeyboardInterrupt: 

### Bidirectional Deep GRU encoder

In [ ]:
## Architecture
hidden_size = 10
input_size = 20
##nn architecture
architecture = ()

In [ ]:
#encoders

deep_gru_encoder_min_forward = DeepGRU(hidden_size, input_size, architecture)
deep_gru_encoder_min_backward = DeepGRU(hidden_size, input_size, architecture)
deep_gru_encoder_min = BidirectionalRNNWithAttention(deep_gru_encoder_min_forward,deep_gru_encoder_min_backward)

deep_gru_encoder_hour_forward = DeepGRU(hidden_size, input_size, architecture)
deep_gru_encoder_hour_backward = DeepGRU(hidden_size, input_size, architecture)
deep_gru_encoder_hour = BidirectionalRNNWithAttention(deep_gru_encoder_hour_forward,deep_gru_encoder_hour_backward)
#fc layer
deep_gru_fc_dst_min = DeepNeuralNetwork(2*hidden_size, pred_length, *architecture)
deep_gru_fc_kp_min = DeepNeuralNetwork(2*hidden_size,hour_to_3_hour(pred_length), *architecture)

deep_gru_fc_dst_hour = DeepNeuralNetwork(2*hidden_size, pred_length, *architecture)
deep_gru_fc_kp_hour = DeepNeuralNetwork(2*hidden_size, hour_to_3_hour(pred_length), *architecture)

In [ ]:
NormalGRU_min = to_device(NormalArchitecture(deep_gru_encoder_min, deep_gru_fc_dst_min, deep_gru_fc_kp_min), device)
NormalGRU_hour = to_device(NormalArchitecture(deep_gru_encoder_hour, deep_gru_fc_dst_hour, deep_gru_fc_kp_hour), device)

In [ ]:
##hyperparameters
epochs = 100
max_lr = 1e-3
weigth_decay = 1e-4
grad_clip = 1e-2
#opt_func = Adam
opt_func = RMSprop

In [ ]:
NormalGRU_min_history = []

In [ ]:
NormalGRU_min_history += NormalGRU_min.fit(epochs, max_lr, train_mn_dl, test_mn_dl, weigth_decay, grad_clip, opt_func)

RuntimeError: bad allocation

In [ ]:
NormalGRU_hour_history = []

In [ ]:
NormalGRU_hour_history += NormalGRU_hour.fit(epochs, max_lr, train_hn_dl, test_hn_dl, weigth_decay, grad_clip, opt_func)

Epoch [0]:
	last_lr: 0.00004
	train_loss: 0.9408
	val_loss: 0.8459


KeyboardInterrupt: 

### Bidirectional Deep Vanilla RNN encoder

In [ ]:
## Architecture
hidden_size = 10
input_size = 20
##nn architecture
architecture = ()

In [ ]:
#encoders
deep_rnn_encoder_min_forward = DeepVanillaRNN(hidden_size, input_size, architecture)
deep_rnn_encoder_min_backward = DeepVanillaRNN(hidden_size, input_size, architecture)
deep_rnn_encoder_min = BidirectionalRNNWithAttention(deep_rnn_encoder_min_forward, deep_rnn_encoder_min_backward)

deep_rnn_encoder_hour_forward = DeepVanillaRNN(hidden_size, input_size, architecture)
deep_rnn_encoder_hour_backward = DeepVanillaRNN(hidden_size, input_size, architecture)
deep_rnn_encoder_hour = BidirectionalRNNWithAttention(deep_rnn_encoder_hour_forward,deep_rnn_encoder_hour_backward)
#fc layer
deep_rnn_fc_dst_min = DeepNeuralNetwork(2*hidden_size, pred_length, *architecture)
deep_rnn_fc_kp_min = DeepNeuralNetwork(2*hidden_size, hour_to_3_hour(pred_length), *architecture)

deep_rnn_fc_dst_hour = DeepNeuralNetwork(2*hidden_size, pred_length, *architecture)
deep_rnn_fc_kp_hour = DeepNeuralNetwork(2*hidden_size, hour_to_3_hour(pred_length), *architecture)

In [ ]:
NormalVanillaRNN_min = to_device(NormalArchitecture(deep_rnn_encoder_min, deep_rnn_fc_dst_min, deep_rnn_fc_kp_min), device)
NormalVanillaRNN_hour = to_device(NormalArchitecture(deep_rnn_encoder_hour, deep_rnn_fc_dst_hour, deep_rnn_fc_kp_hour), device)

In [ ]:
##hyperparameters
epochs = 100
max_lr = 1e-3
weigth_decay = 1e-4
grad_clip = 1e-2
#opt_func = Adam
opt_func = RMSprop

In [ ]:
NormalVanillaRNN_min_history = []

In [ ]:
NormalVanillaRNN_min_history += NormalVanillaRNN_min.fit(epochs, max_lr, train_mn_dl, test_mn_dl, weigth_decay, grad_clip, opt_func)

In [ ]:
NormalVanillaRNN_hour_history = []

In [ ]:
NormalVanillaRNN_hour_history += NormalVanillaRNN_hour.fit(epochs, max_lr, train_hn_dl, test_hn_dl, weigth_decay, grad_clip, opt_func)

Epoch [0]:
	last_lr: 0.00004
	train_loss: 1.3040
	val_loss: 1.0009
Epoch [1]:
	last_lr: 0.00005
	train_loss: 1.0306
	val_loss: 0.9201
Epoch [2]:
	last_lr: 0.00006
	train_loss: 0.9532
	val_loss: 0.8801


KeyboardInterrupt: 

### Non deep bidirectional architectures with attention

#### LSTM

In [ ]:
non_deep_lstm_forward_min = LSTM(input_size, hidden_size)
non_deep_lstm_backward_min = LSTM(input_size, hidden_size)
bidirectional_lstm_encoder_min = BidirectionalRNNWithAttention(non_deep_lstm_forward_min, non_deep_lstm_backward_min)

non_deep_lstm_forward_hour = LSTM(input_size, hidden_size)
non_deep_lstm_backward_hour = LSTM(input_size, hidden_size)
bidirectional_lstm_encoder_hour = BidirectionalRNNWithAttention(non_deep_lstm_forward_hour, non_deep_lstm_backward_hour)
#fc layer
non_deep_lstm_fc_dst_min = DeepNeuralNetwork(2*hidden_size, pred_length, *architecture)
non_deep_lstm_fc_kp_min = DeepNeuralNetwork(2*hidden_size, hour_to_3_hour(pred_length), *architecture)

non_deep_lstm_fc_dst_hour = DeepNeuralNetwork(2*hidden_size, pred_length, *architecture)
non_deep_lstm_fc_kp_hour = DeepNeuralNetwork(2*hidden_size, hour_to_3_hour(pred_length), *architecture)

In [ ]:
NormalNonDeepLSTM_min = to_device(NormalArchitecture(bidirectional_lstm_encoder_min, non_deep_lstm_fc_dst_min, non_deep_lstm_fc_kp_min), device)
NormalNonDeepLSTM_hour = to_device(NormalArchitecture(bidirectional_lstm_encoder_hour, non_deep_lstm_fc_dst_hour, non_deep_lstm_fc_kp_hour), device)

In [ ]:
##hyperparameters
epochs = 100
max_lr = 1e-3
weigth_decay = 1e-4
grad_clip = 1e-2
#opt_func = Adam
opt_func = RMSprop

In [ ]:
NormalNonDeepLSTM_min_history = []

In [ ]:
NormalNonDeepLSTM_min_history += NormalNonDeepLSTM_min.fit(epochs, max_lr, train_mn_dl, test_mn_dl, weigth_decay, grad_clip, opt_func)

In [ ]:
NormalNonDeepLSTM_hour_history = []

In [ ]:
NormalNonDeepLSTM_hour_history += NormalNonDeepLSTM_hour.fit(epochs, max_lr, train_hn_dl, test_hn_dl, weigth_decay, grad_clip, opt_func)

Epoch [0]:
	last_lr: 0.00005
	train_loss: 2.0350
	val_loss: 2.0597
Epoch [1]:
	last_lr: 0.00014
	train_loss: 2.0237
	val_loss: 2.0414
Epoch [2]:
	last_lr: 0.00026
	train_loss: 1.9437
	val_loss: 1.7768


KeyboardInterrupt: 

#### GRU

In [ ]:
non_deep_gru_forward_min = GRU(input_size, hidden_size)
non_deep_gru_backward_min = GRU(input_size, hidden_size)
bidirectional_gru_encoder_min = BidirectionalRNNWithAttention(non_deep_gru_forward_min, non_deep_gru_backward_min)

non_deep_gru_forward_hour = GRU(input_size, hidden_size)
non_deep_gru_backward_hour = GRU(input_size, hidden_size)
bidirectional_gru_encoder_hour = BidirectionalRNNWithAttention(non_deep_gru_forward_hour, non_deep_gru_backward_hour)
#fc layer
non_deep_gru_fc_dst_min = DeepNeuralNetwork(2*hidden_size, pred_length, *architecture)
non_deep_gru_fc_kp_min = DeepNeuralNetwork(2*hidden_size, hour_to_3_hour(pred_length), *architecture)

non_deep_gru_fc_dst_hour = DeepNeuralNetwork(2*hidden_size, pred_length, *architecture)
non_deep_gru_fc_kp_hour = DeepNeuralNetwork(2*hidden_size, hour_to_3_hour(pred_length), *architecture)


In [ ]:
NormalNonDeepGRU_min = to_device(NormalArchitecture(bidirectional_gru_encoder_min, non_deep_gru_fc_dst_min, non_deep_gru_fc_kp_min), device)
NormalNonDeepGRU_hour = to_device(NormalArchitecture(bidirectional_gru_encoder_hour, non_deep_gru_fc_dst_hour, non_deep_gru_fc_kp_hour), device)

In [ ]:
##hyperparameters
epochs = 100
max_lr = 1e-3
weigth_decay = 1e-4
grad_clip = 1e-2
#opt_func = Adam
opt_func = RMSprop

In [ ]:
NormalNonDeepGRU_min_history = []

In [ ]:
NormalNonDeepGRU_min_history += NormalNonDeepGRU_min.fit(epochs, max_lr, train_mn_dl, test_mn_dl, weigth_decay, grad_clip, opt_func)

In [ ]:
NormalNonDeepGRU_hour_history = []

In [ ]:
NormalNonDeepGRU_hour_history += NormalNonDeepGRU_hour.fit(epochs, max_lr, train_hn_dl, test_hn_dl, weigth_decay, grad_clip, opt_func)

Epoch [0]:
	last_lr: 0.00005
	train_loss: 2.1161
	val_loss: 2.1215
Epoch [1]:
	last_lr: 0.00014
	train_loss: 2.0831
	val_loss: 2.0747


KeyboardInterrupt: 

#### RNN

In [ ]:
non_deep_rnn_forward_min = VanillaRNN(input_size, hidden_size)
non_deep_rnn_backward_min = VanillaRNN(input_size, hidden_size)
bidirectional_rnn_encoder_min = BidirectionalRNNWithAttention(non_deep_rnn_forward_min, non_deep_rnn_backward_min)

non_deep_rnn_forward_hour = VanillaRNN(input_size, hidden_size)
non_deep_rnn_backward_hour = VanillaRNN(input_size, hidden_size)
bidirectional_rnn_encoder_hour = BidirectionalRNNWithAttention(non_deep_rnn_forward_hour, non_deep_rnn_backward_hour)
#fc layer
non_deep_rnn_fc_dst_min = DeepNeuralNetwork(2*hidden_size, pred_length, *architecture)
non_deep_rnn_fc_kp_min = DeepNeuralNetwork(2*hidden_size, hour_to_3_hour(pred_length), *architecture)

non_deep_rnn_fc_dst_hour = DeepNeuralNetwork(2*hidden_size, pred_length, *architecture)
non_deep_rnn_fc_kp_hour = DeepNeuralNetwork(2*hidden_size, hour_to_3_hour(pred_length), *architecture)


In [ ]:
NormalNonDeepVanillaRNN_min = to_device(NormalArchitecture(bidirectional_rnn_encoder_min, non_deep_rnn_fc_dst_min, non_deep_rnn_fc_kp_min), device)
NormalNonDeepVanillaRNN_hour = to_device(NormalArchitecture(bidirectional_rnn_encoder_hour, non_deep_rnn_fc_dst_hour, non_deep_rnn_fc_kp_hour), device)

In [ ]:
##hyperparameters
epochs = 100
max_lr = 1e-3
weigth_decay = 1e-4
grad_clip = 1e-2
#opt_func = Adam
opt_func = RMSprop

In [ ]:
NormalNonDeepVanillaRNN_min_history = []

In [ ]:
RefinedNonDeepVanillaRNN_min_history += NormalNonDeepVanillaRNN_min.fit(epochs, max_lr, train_mn_dl, test_mn_dl, weigth_decay, grad_clip, opt_func)

In [ ]:
NormalNonDeepVanillaRNN_hour_history = []

In [ ]:
NormalNonDeepVanillaRNN_hour_history += NormalNonDeepVanillaRNN_hour.fit(epochs, max_lr, train_hn_dl, test_hn_dl, weigth_decay, grad_clip, opt_func)

Epoch [0]:
	last_lr: 0.00005
	train_loss: 2.0527
	val_loss: 2.0624


KeyboardInterrupt: 

# Seq2Seq MultiHead2MultiHead

In [20]:
##hyperparameters
epochs = 10
max_lr = 1e-2
weigth_decay = 1e-6
grad_clip = 1e-1
#opt_func = Adam
opt_func = RMSprop

In [ ]:
architecture = (10,10)

In [21]:
encoder_fc = EncoderMultiheadAttentionGRU(9, hidden_size, 3, architecture)
encoder_mg = EncoderMultiheadAttentionGRU(11, hidden_size, 1, architecture)
fc = DeepNeuralNetwork(2*hidden_size, hour_to_3_hour(pred_length))
model = MultiHead2SingleOUT(encoder_fc, encoder_mg, fc)

In [ ]:
encoder_fc = EncoderMultiheadAttentionGRU(9, hidden_size, 3, architecture)
encoder_mg = EncoderMultiheadAttentionGRU(11, hidden_size, 1, architecture)
model = MultiHeaded2MultiheadAttentionGRU(encoder_fc, encoder_mg, 2, architecture, hour_to_3_hour(pred_length))

In [22]:
new_model = []

In [23]:
new_model+=model.fit(epochs, max_lr, train_hour_kp_dl, test_hour_kp_dl, weigth_decay, grad_clip, opt_func)

RuntimeError: Caught RuntimeError in DataLoader worker process 0.
Original Traceback (most recent call last):
  File "c:\Users\Innotronics\AppData\Local\Programs\Python\Python310\lib\site-packages\torch\utils\data\_utils\worker.py", line 308, in _worker_loop
    data = fetcher.fetch(index)
  File "c:\Users\Innotronics\AppData\Local\Programs\Python\Python310\lib\site-packages\torch\utils\data\_utils\fetch.py", line 54, in fetch
    return self.collate_fn(data)
  File "c:\Users\Innotronics\AppData\Local\Programs\Python\Python310\lib\site-packages\torch\utils\data\_utils\collate.py", line 265, in default_collate
    return collate(batch, collate_fn_map=default_collate_fn_map)
  File "c:\Users\Innotronics\AppData\Local\Programs\Python\Python310\lib\site-packages\torch\utils\data\_utils\collate.py", line 142, in collate
    return [collate(samples, collate_fn_map=collate_fn_map) for samples in transposed]  # Backwards compatibility.
  File "c:\Users\Innotronics\AppData\Local\Programs\Python

# Conclusion